<a href="https://colab.research.google.com/github/enliktjioe/master-thesis-2021/blob/main/sandbox/BERTopic/Copy_of_BERTopic_DTM.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Tutorial** - Dynamic Topic Modeling with Trump's Tweets
(last updated 26-04-2021)

In this tutorial we will be using Dynamic Topic Modeling with BERTopic to visualize how topics in Trump's Tweets have evolved over time. These topics will be visualized and thoroughly explored. 

## Dynamic Topic Models
Dynamic topic models can be used to analyze the evolution of topics of a collection of documents over time. 

<br>

<img src="https://raw.githubusercontent.com/MaartenGr/BERTopic/master/images/logo.png" width="40%">

# Enabling the GPU

First, you'll need to enable GPUs for the notebook:

- Navigate to Edit→Notebook Settings
- select GPU from the Hardware Accelerator drop-down

[Reference](https://colab.research.google.com/notebooks/gpu.ipynb)

# Installing BERTopic

We start by installing BERTopic from PyPi:

In [1]:
%%capture
!pip install bertopic

## Restart the Notebook
After installing BERTopic, some packages that were already loaded were updated and in order to correctly use them, we should now restart the notebook.

From the Menu:

Runtime → Restart Runtime

# **Data**
For this tutorial, we will be needing to extract all Trump's Tweet from his @realDonalTrump account. We will be removing all retweet and focus on his original tweets. 

Moreover, since we are looking at his tweets over time, we will be saving all timestamps related to his tweets.

In [2]:
import re
import pandas as pd
# using bolt google play store manual annotation review
# url='https://drive.google.com/file/d/1R0102hXhlWBmtWr03up4vyRQk5NkQU_l/view?usp=sharing'
# url2='https://drive.google.com/uc?id=' + url.split('/')[-2]

# bolt_google_playstore_review.csv 17MB (21 Dec 2020)
url='https://drive.google.com/file/d/1qWuyf3UrpaU5xnxLmO3GMFa6zybSFYQh/view?usp=sharing'
url2='https://drive.google.com/uc?id=' + url.split('/')[-2]
df = pd.read_csv(url2, usecols=['content','at'])

# remove emoji
# https://stackoverflow.com/a/57514515/2670476
df = df.astype(str).apply(lambda x: x.str.encode('ascii', 'ignore').str.decode('ascii'))

df.content = df.apply(lambda row: re.sub(r"http\S+", "", row.content).lower(), 1)
df.content = df.apply(lambda row: " ".join(filter(lambda x:x[0]!="@", row.content.split())), 1)
df.content = df.apply(lambda row: " ".join(re.sub("[^a-zA-Z]+", " ", row.content).split()), 1)
tweets = df.content.tolist()
timestamps = df['at'].tolist()
# tweets
# timestamps

In [3]:
tweets[0]

'the first thing i noticed is that you can t prenook your trip which isn t great as i had to catch a flight at pm today i decided to give it a go anyway using the instant booking there were drivers available near me and i went to book one of them completed the booking only to find that the driver disappeared and he now was shown as engaged went to book the other one and same happened again unreliable service i will get rid of the app today'

# **Dynamic Topic Modeling**


## Basic Topic Model
To perform Dynamic Topic Modeling with BERTopic we will first need to create a basic topic model using all tweets. The temporal aspect will be ignored as we are, for now, only interested in the topics that reside in those tweets. 

In [4]:
from bertopic import BERTopic
# topic_model = BERTopic(min_topic_size=35, verbose=True)
topic_model = BERTopic(verbose=True)
topics, _ = topic_model.fit_transform(tweets)

2021-05-30 13:03:47,365 - BERTopic - Transformed documents to Embeddings
2021-05-30 13:05:42,238 - BERTopic - Reduced dimensionality with UMAP
2021-05-30 13:05:48,210 - BERTopic - Clustered UMAP embeddings with HDBSCAN


We can then extract most frequent topics:

In [5]:
freq = topic_model.get_topic_info(); freq.head(10)

Topic  Count                                    Name
0     -1  15690        -1_cancelled_address_lost_update
1     11   2315                11_zzcv_gdtak_gdy_gdynua
2    429   2023         429_polite_respectful_kind_calm
3    262   1224       262_enjoy_easier_enjoying_comfort
4     18    955                  18_terrific_gbp_gb_gbe
5    612    915  612_alternative_mins_cheaper_expensive
6      1    837                      1_zzcv_gcc_gde_gdg
7    678    659      678_sms_verification_register_sign
8     46    593                 46_adorable_zzcv_gdy_gd
9     14    578      14_exciting_hot_innovative_amazing

-1 refers to all outliers and should typically be ignored. Next, let's take a look at a frequent topic that were generated:

In [6]:
# topic_nr = freq.iloc[3]["Topic"]  # We select a frequent topic
topic_nr = freq.iloc[2]["Topic"]  # We select a frequent topic
topic_model.get_topic(topic_nr)   # You can select a topic number as shown above

[('polite', 0.007070070683117411),
 ('respectful', 0.0061446189193885324),
 ('kind', 0.004164390122583066),
 ('calm', 0.0032526844233021547),
 ('caring', 0.002487402242568376),
 ('smooth', 0.00229642756875857),
 ('trustworthy', 0.0018602166525322733),
 ('timely', 0.0017636053769346123),
 ('safely', 0.0016995730836847646),
 ('neat', 0.0016279434248627192)]

We can visualize the basic topics that were created with the Intertopic Distance Map. This allows us to judge visually whether the basic topics are sufficient before proceeding to creating the topics over time. 

In [7]:
fig = topic_model.visualize_topics(); fig

## Topics over Time
Before we start with the Dynamic Topic Modeling step, it is important that you are satisfied with the topics that were created previously. We are going to be using those specific topics as a base for Dynamic Topic Modeling. 

Thus, this step will essentially show you how the topics that were defined previously have evolved over time. 

There are a few important parameters that you should take note of, namely:

* `docs`
  * These are the tweets that we are using
* `topics`
  * The topics that we have created before
* `timestamps`
  * The timestamp of each tweet/document
* `global_tuning`
  * Whether to average the topic representation of a topic at time *t* with its global topic representation
* `evolution_tuning`
  * Whether to average the topic representation of a topic at time *t* with the topic representation of that topic at time *t-1*
* `nr_bins`
  * The number of bins to put our timestamps into. It is computationally inefficient to extract the topics at thousands of different timestamps. Therefore, it is advised to keep this value below 20. 


In [8]:
topics_over_time = topic_model.topics_over_time(docs=tweets, 
                                                topics=topics, 
                                                timestamps=timestamps, 
                                                global_tuning=True, 
                                                evolution_tuning=True, 
                                                nr_bins=20)

20it [03:49, 11.47s/it]


## Visualize Topics over Time
After having created our `topics_over_time`, we will have to visualize those topics as accessing them becomes a bit more difficult with the added temporal dimension. 

To do so, we are going to visualize the distribution of topics over time based on their frequency. Doing so allows us to see how the topics have evolved over time. Make sure to hover over any point to see how the topic representation at time *t* differs from the global topic representation. 


In [9]:
topic_model.visualize_topics_over_time(topics_over_time, top_n=20)